# Importing Libraries

In [1]:
# import sklearn
from sklearn.linear_model import LinearRegression

# Importing for Data Manipulation
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Importing For Data Visualization
import plotly.express as px
import plotly.graph_objs as go
from plotly.offline import iplot

# Load Dataset

In [2]:
%store -r df_surplus
df_surplus = df_surplus

In [3]:
# Checking the databased again
df_surplus.describe()

Price       Quantity     CustomerNo
count  522601.000000  522601.000000  522601.000000
mean       12.637160      10.667492   15226.311767
std         7.965974     157.542420    1716.555479
min         5.130000       1.000000   12004.000000
25%        10.990000       1.000000   13804.000000
50%        11.940000       4.000000   15152.000000
75%        14.090000      12.000000   16729.000000
max       660.620000   80995.000000   18287.000000

In [4]:
df_surplus.info()

<class 'pandas.core.frame.DataFrame'>
Index: 522601 entries, 0 to 536324
Data columns (total 8 columns):
 #   Column         Non-Null Count   Dtype  
---  ------         --------------   -----  
 0   TransactionNo  522601 non-null  object 
 1   Date           522601 non-null  object 
 2   ProductNo      522601 non-null  object 
 3   ProductName    522601 non-null  object 
 4   Price          522601 non-null  float64
 5   Quantity       522601 non-null  int64  
 6   CustomerNo     522601 non-null  float64
 7   Country        522601 non-null  object 
dtypes: float64(2), int64(1), object(5)
memory usage: 35.9+ MB


In [5]:
# Changing the type 'Date' to datetime
df_surplus['Date'] = pd.to_datetime(df_surplus['Date'])

In [6]:
# Changing the data type 'CustomerNo' and 'TransactionId' into integer
df_surplus['CustomerNo'] = df_surplus['CustomerNo'].astype(int)
df_surplus['TransactionNo'] = df_surplus['TransactionNo'].astype(int)

In [7]:
#Let's check it again
df_surplus.info()

<class 'pandas.core.frame.DataFrame'>
Index: 522601 entries, 0 to 536324
Data columns (total 8 columns):
 #   Column         Non-Null Count   Dtype         
---  ------         --------------   -----         
 0   TransactionNo  522601 non-null  int32         
 1   Date           522601 non-null  datetime64[ns]
 2   ProductNo      522601 non-null  object        
 3   ProductName    522601 non-null  object        
 4   Price          522601 non-null  float64       
 5   Quantity       522601 non-null  int64         
 6   CustomerNo     522601 non-null  int32         
 7   Country        522601 non-null  object        
dtypes: datetime64[ns](1), float64(1), int32(2), int64(1), object(3)
memory usage: 31.9+ MB


# Exploratory Data Analysis (EDA)

First we need to set the time of database for being analyze

In [8]:
# Setting the date and time
start_date = df_surplus.Date.min()
end_date = df_surplus.Date.max()
period = end_date - start_date

print("Start:", start_date)
print("End:", end_date)
print("Period:", period)

Start: 2018-12-01 00:00:00
End: 2019-12-09 00:00:00
Period: 373 days 00:00:00


In [9]:
# Creating Revenue Collumn
df_surplus['Revenue'] = df_surplus['Price'] * df_surplus['Quantity']
df_surplus.sample()

TransactionNo       Date ProductNo                       ProductName  \
60588         577258 2019-11-18     21810  Christmas Hanging Star With Bell   

       Price  Quantity  CustomerNo         Country  Revenue  
60588  10.65         2       16764  United Kingdom     21.3

In [10]:
# Memisah tanggal, bulan dan tahun
df_surplus['Day'] = pd.DatetimeIndex(df_surplus['Date']).day
df_surplus['Month'] = pd.DatetimeIndex(df_surplus['Date']).month.astype(int)
df_surplus['Year'] = pd.DatetimeIndex(df_surplus['Date']).year
df_surplus['Month-Year'] = df_surplus['Date'].apply(lambda x: x.strftime('%Y-%m'))

In [11]:
df_surplus['Month-Year'].describe()

count      522601
unique         13
top       2019-11
freq        81819
Name: Month-Year, dtype: object

In [12]:
# bulanan
mountly_revenue = df_surplus.groupby(['Month-Year'])['Revenue'].sum().reset_index()
mountly_revenue = mountly_revenue.sort_values(by=['Month-Year'], ascending = True)
fig1 = px.line(mountly_revenue, x="Month-Year", y="Revenue", text="Revenue")
fig1.update_traces(textposition="bottom right")
fig1.show()

In [13]:
df_linear = df_surplus.drop(['ProductName'], axis=1)
df_linear = df_linear.drop(['Date'], axis=1)

In [14]:
df_linear.loc[df_surplus['ProductNo'] == '22139']

TransactionNo ProductNo  Price  Quantity  CustomerNo         Country  \
155            581486     22139   6.04         6       17001  United Kingdom   
1094           581498     22139   6.19         2       14498  United Kingdom   
1433           581570     22139   6.19         3       12662         Germany   
1830           581217     22139   6.19         1       16217  United Kingdom   
2850           581219     22139   7.24         2       16219  United Kingdom   
...               ...       ...    ...       ...         ...             ...   
520364         537624     22139  15.32         1       12748  United Kingdom   
520468         537633     22139  15.32         1       17633  United Kingdom   
520483         537634     22139  15.32         2       16775  United Kingdom   
531108         536982     22139  21.55        10       14982  United Kingdom   
533367         536381     22139  14.61        23       15311  United Kingdom   

        Revenue  Day  Month  Year Month-Year  
155       36.24    9     12  2019    2019-12  
1094      12.38    9     12  2019    2019-12  
1433      18.57    9     12  2019    2019-12  
1830       6.19    8     12  2019    2019-12  
2850      14.48    8     12  2019    2019-12  
...         ...  ...    ...   ...        ...  
520364    15.32    7     12  2018    2018-12  
520468    15.32    7     12  2018    2018-12  
520483    30.64    7     12  2018    2018-12  
531108   215.50    3     12  2018    2018-12  
533367   336.03    1     12  2018    2018-12  

[965 rows x 11 columns]

In [15]:
df_country = df_surplus["Country"].copy()
df_country = df_country.drop_duplicates().sort_values(ascending = True, ignore_index=True)
dict_country = {}
idx1 = 1
for key in df_country:
    dict_country[key] = idx1
    idx1+=1
dict_country

{'Australia': 1,
 'Austria': 2,
 'Bahrain': 3,
 'Belgium': 4,
 'Brazil': 5,
 'Canada': 6,
 'Channel Islands': 7,
 'Cyprus': 8,
 'Czech Republic': 9,
 'Denmark': 10,
 'EIRE': 11,
 'European Community': 12,
 'Finland': 13,
 'France': 14,
 'Germany': 15,
 'Greece': 16,
 'Hong Kong': 17,
 'Iceland': 18,
 'Israel': 19,
 'Italy': 20,
 'Japan': 21,
 'Lebanon': 22,
 'Lithuania': 23,
 'Malta': 24,
 'Netherlands': 25,
 'Norway': 26,
 'Poland': 27,
 'Portugal': 28,
 'RSA': 29,
 'Saudi Arabia': 30,
 'Singapore': 31,
 'Spain': 32,
 'Sweden': 33,
 'Switzerland': 34,
 'USA': 35,
 'United Arab Emirates': 36,
 'United Kingdom': 37,
 'Unspecified': 38}

In [16]:
df_normal = pd.DataFrame(df_surplus.copy())
df_normal = df_normal.replace({"Country": dict_country})
df_normal = df_normal.drop(["ProductName", "Date"], axis=1)
df_normal

TransactionNo ProductNo  Price  Quantity  CustomerNo  Country  \
0              581482     22485  21.47        12       17490       37   
1              581475     22596  10.65        36       13069       37   
2              581475     23235  11.53        12       13069       37   
3              581475     23272  10.65        12       13069       37   
4              581475     23239  11.94         6       13069       37   
...               ...       ...    ...       ...         ...      ...   
536320         536585     37449  20.45         2       17460       37   
536321         536590     22776  20.45         1       13065       37   
536322         536590     22622  20.45         2       13065       37   
536323         536591     37449  20.45         1       14606       37   
536324         536597     22220  20.45         1       18011       37   

        Revenue  Day  Month  Year Month-Year  
0        257.64    9     12  2019    2019-12  
1        383.40    9     12  2019    2019-12  
2        138.36    9     12  2019    2019-12  
3        127.80    9     12  2019    2019-12  
4         71.64    9     12  2019    2019-12  
...         ...  ...    ...   ...        ...  
536320    40.90    1     12  2018    2018-12  
536321    20.45    1     12  2018    2018-12  
536322    40.90    1     12  2018    2018-12  
536323    20.45    1     12  2018    2018-12  
536324    20.45    1     12  2018    2018-12  

[522601 rows x 11 columns]

In [17]:
df_normal.loc[df_normal['ProductNo'] == '22915']

TransactionNo ProductNo  Price  Quantity  CustomerNo  Country  \
900            581493     22915   7.24        12       12423        4   
1574           581585     22915   7.24        24       15804       37   
3430           581238     22915   6.19         6       16238       37   
3513           581241     22915   6.19       120       15520       37   
6779           581015     22915   6.19        24       13949       37   
...               ...       ...    ...       ...         ...      ...   
529678         536876     22915  15.44         1       12876        4   
532383         536778     22915  10.68        24       13138       37   
533442         536388     22915  10.68        12       16250       37   
535300         536568     22915  10.68        12       16048       37   
535897         536592     22915  15.44         1       16592       37   

        Revenue  Day  Month  Year Month-Year  
900       86.88    9     12  2019    2019-12  
1574     173.76    9     12  2019    2019-12  
3430      37.14    8     12  2019    2019-12  
3513     742.80    8     12  2019    2019-12  
6779     148.56    7     12  2019    2019-12  
...         ...  ...    ...   ...        ...  
529678    15.44    3     12  2018    2018-12  
532383   256.32    2     12  2018    2018-12  
533442   128.16    1     12  2018    2018-12  
535300   128.16    1     12  2018    2018-12  
535897    15.44    1     12  2018    2018-12  

[186 rows x 11 columns]

In [25]:
# Kelompokkan data berdasarkan CustomerNo dan TransactionNo, lalu hitung jumlah kemunculan TransactionNo
customer_transaction_counts = df_normal.groupby(['CustomerNo', 'TransactionNo']).size().reset_index(name='Count')

# customer_transaction_counts.loc[customer_transaction_counts['CustomerNo'] == 18283]

# Temukan CustomerNo dengan TransactionNo terbanyak dalam 1 Transaksi
most_frequent_customer = customer_transaction_counts['CustomerNo'][customer_transaction_counts['Count'].idxmax()]

print("CustomerNo yang paling sering melakukan TransactionNo:", most_frequent_customer)

CustomerNo yang paling sering melakukan TransactionNo: 14585


In [19]:
# Customer dengan Transaksi terbanyak
total_count_by_customer = customer_transaction_counts.groupby('CustomerNo')['Count'].sum().reset_index()
total_count_by_customer

total_count_by_customer.sort_values(by="Count", ascending=False)


CustomerNo  Count
4384       17841   7671
2085       14911   5574
1458       14096   5093
408        12748   4413
1851       14606   2670
...          ...    ...
800        13256      1
813        13270      1
2578       15524      1
3308       16454      1
4448       17923      1

[4718 rows x 2 columns]

In [20]:
# Creating TrackRecord Collumn
df_normal.loc[df_normal['CustomerNo'] == 12423].count()
# df_surplus['TrackRecord'] = df_surplus.groupby(['TransactionNo']).count()
# df_surplus.sample()

TransactionNo    149
ProductNo        149
Price            149
Quantity         149
CustomerNo       149
Country          149
Revenue          149
Day              149
Month            149
Year             149
Month-Year       149
dtype: int64

In [21]:
# # Top 10 Pelanggan

# top_customer = df_surplus.groupby(["CustomerNo"])['TrackRecord'].sum().reset_index()
# top_customer = top_customer.sort_values(by=['CustomerNo'], ascending = True, ignore_index=True)
# top_customer

In [22]:
# Mencari Top 10 Penjualan Dataset

top_mountly = df_surplus.groupby(['Month-Year', "ProductName"])['Quantity'].sum().reset_index()
top_mountly = top_mountly.sort_values(by=['Month-Year'], ascending = True, ignore_index=True)
top_mountly

Month-Year                       ProductName  Quantity
0        2018-12            10 Colour Spaceboy Pen       590
1        2018-12                Pink Padded Mobile        13
2        2018-12       Pink Painted Kashmiri Chair         4
3        2018-12        Pink Paisley Cushion Cover         4
4        2018-12       Pink Paisley Rose Gift Wrap        75
...          ...                               ...       ...
33186    2019-12           Gingham Recipe Book Box        29
33187    2019-12              Giraffe Wooden Ruler        81
33188    2019-12    Girls Alphabet Iron On Patches       146
33189    2019-12                     Glamorous Mug        49
33190    2019-12  Zinc Wire Sweetheart Letter Tray        13

[33191 rows x 3 columns]

In [23]:
top_mountly.sort_values(['Month-Year', "ProductName", "Quantity"], ascending=[True, True, False])\
  .groupby(['Month-Year']).head(10)

Month-Year                          ProductName  Quantity
0        2018-12               10 Colour Spaceboy Pen       590
1795     2018-12           12 Coloured Party Balloons        62
1796     2018-12            12 Daisy Pegs In Wood Box        12
1797     2018-12            12 Egg House Painted Wood        11
1798     2018-12     12 Ivory Rose Peg Place Settings        22
...          ...                                  ...       ...
32384    2019-12        12 Pencil Small Tube Woodland       284
32385    2019-12  12 Pencils Small Tube Red Retrospot       300
32386    2019-12          12 Pencils Small Tube Skull        12
32387    2019-12   12 Pencils Tall Tube Red Retrospot        60
32388    2019-12          12 Pencils Tall Tube Skulls       103

[130 rows x 3 columns]

In [27]:
fig2 = px.bar(top_mountly, x="Month-Year", y="Quantity", color="ProductName")
fig2.update_layout(xaxis=dict(type = "category"))
fig2.show()

Pendapatan Tertinggi di Tahun 2019 bulan 11

In [ ]:
# Mencari Bottom 5 Penjualan Dataset

top_mountly.tail(5)

In [ ]:
fig3 = px.bar(top5_mountly.tail(5), x="Month-Year", y="Revenue", text="Revenue")
fig3.update_layout(xaxis=dict(type = "category"))
fig3.show()

Pendapatan Terendah di Tahun 2019 bulan 12

In [ ]:
# Penjualan bulanan berdasarkan negara

test1 = df_surplus.groupby(['Country', 'Month-Year'])['Revenue'].sum().reset_index()
fig3 = px.line(test1, x="Month-Year", y="Revenue", color="Country")
fig3.update_traces(textposition="bottom right")
fig3.show()

In [ ]:
fig3 = px.bar(test1, x="Month-Year", y="Revenue", title="Wide-Form Input", color="Country")
fig3.show()

In [ ]:
# Grouping Country and Revenue
top_revenue = df_surplus.groupby(['Country'])['Revenue'].sum().reset_index()
top_revenue = top_revenue.sort_values(by=['Revenue'], ascending = False)

# Creating Diagram Bar to determine which country has top revenue
fig = px.bar(top_revenue.head(5), x='Country', y='Revenue', color='Revenue', title='Highest Revenue Countries')
fig.update_xaxes(title='Country')
fig.update_yaxes(title='Revenue')
fig.show()

as you guys can see... the highest revenue in this databased is United Kingdom with **52346795**.

In [ ]:
# Searching Total Product in Database
print('Total Product on this Database:\n' + str(df_surplus['ProductName'].nunique()))

In [ ]:
# Grouping ProductName with Quantity
top_product = df_surplus.groupby(['ProductName'])['Quantity'].sum().reset_index()
top_product = top_product.sort_values(by=['Quantity'], ascending = False)

# Creating Diagram Bar to determine which country has top revenue
fig = px.bar(top_product.head(10), x='ProductName', y='Quantity', color='Quantity', title='Top Product Based on Quantity')
fig.update_xaxes(title='Product Name')
fig.update_yaxes(title='Total Quantity Sold')
fig.show()

In [ ]:
# Grouping ProductName with Revenue
top_product = df_surplus.groupby(['ProductName'])['Revenue'].sum().reset_index()
top_product = top_product.sort_values(by=['Revenue'], ascending = False)

# Creating Diagram Bar to determine which country has top revenue
fig = px.bar(top_product.head(10), x='ProductName', y='Revenue', color='Revenue', title='Top Product Based on Revenue')
fig.update_xaxes(title='Product Name')
fig.update_yaxes(title='Total Revenue')
fig.show()

In [ ]:
# Searching Total Customer in Database
print('Total Customer on this Database:\n' + str(df_surplus['CustomerNo'].nunique()))

In [ ]:
# Grouping CustomerNo with Quantity
top_customer_by_quantity = df_surplus.groupby(['CustomerNo'])['Quantity'].sum().reset_index()
top_customer_by_quantity = top_customer_by_quantity.sort_values(by=['Quantity'], ascending = False)

# Horizontal bar plot for top customers by quantity
fig_customer_quantity = px.bar(top_customer_by_quantity.head(10), x="Quantity", y="CustomerNo", color="Quantity", orientation='h', title="Top Customers according to Product Quantity Sold")
fig_customer_quantity.update_xaxes(title="Quantity")
fig_customer_quantity.update_yaxes(title="CustomerNo", type = 'category')
fig_customer_quantity.show()

In [ ]:
# Grouping CustomerNo with Revenue
top_customer_by_revenue = df_surplus.groupby(['CustomerNo'])['Revenue'].sum().reset_index()
top_customer_by_revenue = top_customer_by_revenue.sort_values(by=['Revenue'], ascending = False)

# Horizontal bar plot for top customers by quantity
fig_customer_revenue = px.bar(top_customer_by_revenue.head(10), x="Revenue", y="CustomerNo", color="Revenue", orientation='h', title="Top Customers according to Revenue")
fig_customer_revenue.update_xaxes(title="Revenue")
fig_customer_revenue.update_yaxes(title="CustomerNo", type = 'category')
fig_customer_revenue.show()